## Volatility exploration notebook

This notebook is a playground for exploring different approaches to **volatility estimation and forecasting**. The goal is to build intuition for how various models behave on historical data and to compare their forecasts against realized volatility.

In [64]:
# this is ugly, but i dont know how to make it better
import sys, os
sys.path.append(os.path.abspath(".."))

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.ticker as mtick
import plotly.io as pio
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from models.volatility.target import log_returns, realized_future_vol
from models.volatility.estimator import close_to_close_vol, parkinson_vol, rs_vol
from models.volatility.forecast import GARCHVolatilityForecaster

import seaborn as sns

from pathlib import Path
from datetime import datetime

plt.style.use('seaborn-v0_8')
sns.set_palette("husl")
plt.rcParams['figure.figsize'] = (16, 12)
pd.set_option('display.max_columns', None)

Given the parsed spot price data set (in this case here given hourly), we compute the hourly and/or daily close to close log-returns.

In [65]:
spot = Path('../data/parsed/spot/BTCUSDT_1h.feather')

df = pd.read_feather(spot)

df["datetime"] = pd.to_datetime(df["datetime"], utc=True)
df = df.set_index("datetime").sort_index()

# Hourly log returns
r_hourly = log_returns(df, "hourly")
r_hourly = r_hourly.dropna() # remove first NaN
print("\n--- Hourly log returns ---")
print(r_hourly.head())

# Daily log returns
r_daily = log_returns(df, "daily")
r_daily = r_daily.dropna() # remove first NaN
print("\n--- Daily log returns ---")
print(r_daily.head())


--- Hourly log returns ---
datetime
2019-03-30 01:00:00+00:00   -0.002372
2019-03-30 02:00:00+00:00   -0.000430
2019-03-30 03:00:00+00:00   -0.006429
2019-03-30 04:00:00+00:00   -0.002443
2019-03-30 05:00:00+00:00    0.004913
Name: logret_hourly, dtype: float64

--- Daily log returns ---
datetime
2019-03-31 00:00:00+00:00   -0.000736
2019-04-01 00:00:00+00:00    0.009847
2019-04-02 00:00:00+00:00    0.158684
2019-04-03 00:00:00+00:00    0.015386
2019-04-04 00:00:00+00:00   -0.006905
Freq: D, Name: logret_daily, dtype: float64


We will distinguish between three forms of volatility:

- **Realized Volatility**  
  - A backward-looking measure based on historical returns.  
  - Answers: *“How much did the asset actually move?”*  
  - Computed from past data (e.g., daily log returns or other OHLC estimators).  
  - Serves as the benchmark or "ground truth" for evaluating forecasts.

- **Forecasted Volatility**  
  - A forward-looking estimate produced by statistical models.  
  - Answers: *“How much do we expect the asset to move in the future?”*  
  - Can be as simple as a rolling standard deviation, or as advanced as GARCH.  
  - Used to generate trading signals (e.g., comparing FV to implied vol).

- **Implied Volatility**  
  - The market’s expectation of future volatility, inferred from option prices.  
  - Answers: *“How much volatility is priced into options today?”*  
  - Not a forecast in itself, but the consensus risk premium implied by supply and demand in the options market.

Volatility is not directly observable, it must be estimated from price data. **Realized volatility (RV)** is a backward-looking measure of how much the underlying asset actually fluctuated over a given time horizon.

There are multiple ways to estimate RV:

- **Close-to-Close**: based only on daily returns between closing prices.  
- **Parkinson (1980)**: uses the daily high–low range, making it more efficient under the assumption of zero drift.  
- **Garman–Klass (1980)**: incorporates open, high, low, and close prices for improved efficiency.  
- **Rogers–Satchell (1991)**: also uses OHLC data but is robust to drift, making it more suitable for trending assets like crypto.  

Each estimator provides a slightly different perspective on “true” volatility.  
Comparing them helps us understand the limitations of relying on any single measure.

### Constructing Realized Volatility Targets

We consider the **forward-looking realized volatility** as the benchmark target for forecast evaluation. For each timestamp $t$, the function looks ahead to the next $h$ periods $(t+1, \dots, t+h)$, computes their realized variance, annualizes it, and aligns the result back to time $t$:

$$
RV_{t,h} \;=\; 
\sqrt{ \frac{ann}{h} \sum_{i=1}^{h} r_{t+i}^{2} }
$$

where  

- $r_{t+i}$ = log-return at step $t+i$  
- $h$ = forecast horizon (hours or days)  
- $ann$ = annualization factor (8760 for hourly, 365 for daily)

---

**Usage examples:**

```python
# Hourly horizon: next 2 hours volatility (annualized, %)
y_2h = realized_future_vol(df, h=2, freq="hourly")

# Hourly horizon: next 24 hours volatility (annualized, %)
y_24h = realized_future_vol(df, h=24, freq="hourly")

# Daily horizon: next 7 days volatility (annualized, %)
y_7d = realized_future_vol(df, h=7, freq="daily")

# Daily horizon: next 30 days volatility (annualized, %)
y_30d = realized_future_vol(df, h=30, freq="daily")



In [66]:
y_2h = realized_future_vol(df, h=2, freq="hourly")
print(y_2h.head())

y_24h = realized_future_vol(df, h=24, freq="hourly")
print(y_24h.head())

y_7d = realized_future_vol(df, h=7, freq="daily")
print(y_7d.head())

y_30d = realized_future_vol(df, h=30, freq="daily")
print(y_30d.head())

datetime
2019-03-30 00:00:00+00:00    15.956558
2019-03-30 01:00:00+00:00    42.640374
2019-03-30 02:00:00+00:00    45.515144
2019-03-30 03:00:00+00:00    36.312275
2019-03-30 04:00:00+00:00    33.407712
Name: rv_vol_future_2h_pct, dtype: float64
datetime
2019-03-30 00:00:00+00:00    22.305981
2019-03-30 01:00:00+00:00    21.842532
2019-03-30 02:00:00+00:00    22.419329
2019-03-30 03:00:00+00:00    19.494366
2019-03-30 04:00:00+00:00    18.951532
Name: rv_vol_future_24h_pct, dtype: float64
datetime
2019-03-30 00:00:00+00:00    116.621635
2019-03-31 00:00:00+00:00    117.981616
2019-04-01 00:00:00+00:00    118.129591
2019-04-02 00:00:00+00:00     31.156059
2019-04-03 00:00:00+00:00     36.399156
Freq: D, Name: rv_vol_future_7d_pct, dtype: float64
datetime
2019-03-30 00:00:00+00:00    66.300587
2019-03-31 00:00:00+00:00    66.524698
2019-04-01 00:00:00+00:00    66.560295
2019-04-02 00:00:00+00:00    37.631337
2019-04-03 00:00:00+00:00    41.081517
Freq: D, Name: rv_vol_future_30d_pct, dt

In [67]:
# --- Hourly data ---
y_2h  = realized_future_vol(df, h=2,  freq="hourly", percent=True)
y_24h = realized_future_vol(df, h=24, freq="hourly", percent=True)

# --- Daily data ---
y_7d  = realized_future_vol(df, h=7,  freq="daily", percent=True)
y_30d = realized_future_vol(df, h=30, freq="daily", percent=True)

# Create subplots
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=(
        "Next 2h Realized Volatility (annualized, %) from hourly returns",
        "Next 24h Realized Volatility (annualized, %) from hourly returns",
        "Next 7d Realized Volatility (annualized, %) from daily returns",
        "Next 30d Realized Volatility (annualized, %) from daily returns"
    )
)

# Add traces for hourly data
fig.add_trace(
    go.Scatter(x=y_2h.index, y=y_2h, mode="lines", name="2h", line=dict(color="blue", width=1.1)),
    row=1, col=1
)
fig.add_trace(
    go.Scatter(x=y_24h.index, y=y_24h, mode="lines", name="24h", line=dict(color="orange", width=1.1)),
    row=1, col=2
)

# Add traces for daily data
fig.add_trace(
    go.Scatter(x=y_7d.index, y=y_7d, mode="lines", name="7d", line=dict(color="green", width=1.1)),
    row=2, col=1
)
fig.add_trace(
    go.Scatter(x=y_30d.index, y=y_30d, mode="lines", name="30d", line=dict(color="red", width=1.1)),
    row=2, col=2
)

# Update layout
fig.update_layout(
    title="Realized Volatility at Different Horizons",
    height=800,
    width=1200,
    template="plotly_white",
    showlegend=False,
    yaxis=dict(tickformat=".0f"),
    xaxis_title="Date",
    yaxis_title="Volatility (%)"
)

fig.show()

The plots above illustrate realized volatility at different horizons (2h, 24h, 7d, 30d). We can clearly see that:

- **Short horizons (2h, 24h)** are very noisy, with volatility frequently spiking to extreme levels (over 1000% annualized). This reflects the high sensitivity of short-term returns to sudden price moves.  
- **Medium horizons (7d)** smooth out much of the noise, but still capture occasional volatility shocks, especially around major market events.  
- **Long horizons (30d)** are the smoothest series. They reveal persistent volatility regimes (high vs. low volatility periods), and extreme short-term noise is averaged out.

Overall, realized volatility becomes less noisy and more persistent as the horizon increases. Short-term volatility is dominated by noise and jumps, while longer horizons capture structural shifts in the market.

Of course, we cannot use **realized future volatility** in a trading backtest — doing so would be cheating, since it requires knowledge of returns that have not yet occurred. Instead, in real time we must rely on **estimators** of volatility, which use only past and current price information. In the following, we will introduce three estimators that give us a way to approximate the underlying volatility process without looking into the future.



The `close_to_close_vol()` function prepares volatility data from raw spot prices. It resamples the series to daily (or hourly) closes, computes log returns, and then estimates realized volatility using a simple *rolling window*. The result is annualized and expressed in percent.

In [68]:
# Daily 30-day window
daily = close_to_close_vol(df, window=30, freq="daily")
display(daily.tail())

# Hourly 24-hour window
hourly = close_to_close_vol(df, window=24, freq="hourly")
display(hourly.tail())

datetime
2025-07-16 00:00:00+00:00    29.722312
2025-07-17 00:00:00+00:00    28.397649
2025-07-18 00:00:00+00:00    28.855147
2025-07-19 00:00:00+00:00    28.822057
2025-07-20 00:00:00+00:00    28.365997
Freq: D, Name: rv_est_pct, dtype: float64

datetime
2025-07-20 19:00:00+00:00    15.246579
2025-07-20 20:00:00+00:00    14.513043
2025-07-20 21:00:00+00:00    14.602468
2025-07-20 22:00:00+00:00    16.784689
2025-07-20 23:00:00+00:00    17.053145
Name: rv_est_pct, dtype: float64

While close-to-close returns give us a simple starting point, they are not the most efficient way to measure volatility. In fact, much more information is available in the data: daily highs and lows capture the full trading range, and intraday returns (e.g., hourly) provide an even finer picture of realized variance.  

By incorporating these richer sources of information, we can construct better (or simply different) volatility estimators.

### Using the full OHLC Data for Volatility Estimation

Since crypto trades 24/7, we can rely on the full daily range of prices (Open, High, Low, Close) to build other volatility estimators than close-to-close returns. Two relevant estimators in this setting are:

- Parkinson Volatility: Uses only the daily high–low range. Under continuous trading (like crypto), this estimator is highly efficient because it captures the full intraday variability without being affected by drift.

- Rogers–Satchell Volatility: Incorporates open, high, low, and close. Unlike Parkinson, it is robust to drift, making it better suited for trending markets such as BTC.

In [69]:
daily_parkinson = parkinson_vol(df, window=30, freq="daily")
display(daily_parkinson.tail())

hourly_parkinson = parkinson_vol(df, window=24, freq="hourly")
display(hourly_parkinson.tail())

datetime
2025-07-16 00:00:00+00:00    33.958816
2025-07-17 00:00:00+00:00    33.402788
2025-07-18 00:00:00+00:00    33.893990
2025-07-19 00:00:00+00:00    33.864038
2025-07-20 00:00:00+00:00    33.084297
Freq: D, Name: rv_parkinson_pct, dtype: float64

datetime
2025-07-20 19:00:00+00:00    17.558650
2025-07-20 20:00:00+00:00    17.507187
2025-07-20 21:00:00+00:00    16.929794
2025-07-20 22:00:00+00:00    22.666494
2025-07-20 23:00:00+00:00    23.338152
Freq: h, Name: rv_parkinson_pct, dtype: float64

In [70]:
daily_rs   = rs_vol(df, window=30, freq="daily")
hourly_rs  = rs_vol(df, window=24, freq="hourly")

display(daily_rs.tail())
display(hourly_rs.tail())

datetime
2025-07-16 00:00:00+00:00    35.105556
2025-07-17 00:00:00+00:00    34.755459
2025-07-18 00:00:00+00:00    35.324271
2025-07-19 00:00:00+00:00    35.275870
2025-07-20 00:00:00+00:00    34.305580
Freq: D, Name: rv_rs_pct, dtype: float64

datetime
2025-07-20 19:00:00+00:00    19.006581
2025-07-20 20:00:00+00:00    19.215264
2025-07-20 21:00:00+00:00    18.141130
2025-07-20 22:00:00+00:00    27.085093
2025-07-20 23:00:00+00:00    27.885140
Freq: h, Name: rv_rs_pct, dtype: float64

We see that all three move together and capture the same volatility regimes, but their levels differ: Close-to-Close tends to underestimate, RS is typically higher, and Parkinson sits in between. This highlights the trade-off between simplicity and information content: adding intraday data yields richer, less noisy estimates of realized volatility.

In [71]:
# Merge into one DataFrame
est_daily = pd.concat(
    [
        daily.rename("rv_est_pct"),
        daily_parkinson.rename("rv_parkinson_pct"),
        daily_rs.rename("rv_rs_pct"),
    ],
    axis=1
).dropna()

fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=est_daily.index, y=est_daily["rv_est_pct"],
        mode="lines", name="Close-to-Close",
        line=dict(color="blue", width=1.3)
    )
)
fig.add_trace(
    go.Scatter(
        x=est_daily.index, y=est_daily["rv_parkinson_pct"],
        mode="lines", name="Parkinson",
        line=dict(color="orange", width=1.3)
    )
)
fig.add_trace(
    go.Scatter(
        x=est_daily.index, y=est_daily["rv_rs_pct"],
        mode="lines", name="Rogers–Satchell",
        line=dict(color="green", width=1.3)
    )
)

fig.update_layout(
    title="Daily 30d Volatility Estimators — Close-to-Close vs Parkinson vs RS",
    xaxis_title="Date",
    yaxis_title="Volatility (%)",
    yaxis=dict(tickformat=".0f"),
    template="plotly_white",
    height=600,
    width=1000,
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1)
)

fig.show()

In [81]:
# Parameters
horizon = 30  # forecast horizon in days

# Benchmark: realized future volatility (forward-looking)
rv_future = realized_future_vol(df, h=horizon, freq="daily", percent=True)

# Estimators (backward-looking)
rv_close = close_to_close_vol(df, window=horizon, freq="daily")
rv_pk    = parkinson_vol(df, window=horizon)
rv_rs    = rs_vol(df, window=horizon)

# Combine for alignment
df_compare = (
    pd.concat([rv_future, rv_close, rv_pk, rv_rs], axis=1)
    .dropna()
    .rename(columns={
        rv_future.name: "Realized Future Vol",
        rv_close.name: "Close-to-Close",
        rv_pk.name: "Parkinson",
        rv_rs.name: "Rogers–Satchell"
    })
)

# Create subplots
fig = make_subplots(
    rows=1, cols=3, shared_yaxes=True,
    subplot_titles=(
        f"Close-to-Close vs Realized ({horizon}d)",
        f"Parkinson vs Realized ({horizon}d)",
        f"Rogers–Satchell vs Realized ({horizon}d)"
    )
)

# --- Subplot 1: Close-to-Close ---
fig.add_trace(go.Scatter(
    x=df_compare.index, y=df_compare["Realized Future Vol"],
    mode="lines", name="Realized Future Vol",
    line=dict(color="black", width=2)
), row=1, col=1)

fig.add_trace(go.Scatter(
    x=df_compare.index, y=df_compare["Close-to-Close"],
    mode="lines", name="Close-to-Close",
    line=dict(width=1.5)
), row=1, col=1)

# --- Subplot 2: Parkinson ---
fig.add_trace(go.Scatter(
    x=df_compare.index, y=df_compare["Realized Future Vol"],
    mode="lines", showlegend=False,
    line=dict(color="black", width=2)
), row=1, col=2)

fig.add_trace(go.Scatter(
    x=df_compare.index, y=df_compare["Parkinson"],
    mode="lines", name="Parkinson",
    line=dict(width=1.5)
), row=1, col=2)

# --- Subplot 3: Rogers–Satchell ---
fig.add_trace(go.Scatter(
    x=df_compare.index, y=df_compare["Realized Future Vol"],
    mode="lines", showlegend=False,
    line=dict(color="black", width=2)
), row=1, col=3)

fig.add_trace(go.Scatter(
    x=df_compare.index, y=df_compare["Rogers–Satchell"],
    mode="lines", name="Rogers–Satchell",
    line=dict(width=1.5)
), row=1, col=3)

# Layout
fig.update_layout(
    title=f"Volatility Estimators vs Realized Future Volatility ({horizon}-day horizon)",
    yaxis_title="Volatility (annualized %)",
    xaxis_title="Date",
    template="plotly_white",
    legend=dict(orientation="h", x=0, y=-0.2)
)

fig.show()

This allows us to evaluate which estimator provides the most accurate real-time proxy for the volatility that ultimately materialized.

Next, we will introduce some forecasting methods and apply them to our estimators.

Question: How should the forecast then be outputted in order to use them in the backtest?


In [72]:
returns_daily = log_returns(df, out_freq="daily")  # for GARCH

returns_daily = returns_daily.dropna()

print(returns_daily)

garch_forecaster = GARCHVolatilityForecaster(returns_daily)
garch_forecaster.fit()

print("1d forecast:", garch_forecaster.forecast(1))
print("5d forecast:", garch_forecaster.forecast(5))
print("21d forecast:", garch_forecaster.forecast(21))

datetime
2019-03-31 00:00:00+00:00   -0.000736
2019-04-01 00:00:00+00:00    0.009847
2019-04-02 00:00:00+00:00    0.158684
2019-04-03 00:00:00+00:00    0.015386
2019-04-04 00:00:00+00:00   -0.006905
                               ...   
2025-07-16 00:00:00+00:00    0.007381
2025-07-17 00:00:00+00:00    0.004601
2025-07-18 00:00:00+00:00   -0.010567
2025-07-19 00:00:00+00:00   -0.000720
2025-07-20 00:00:00+00:00   -0.004890
Freq: D, Name: logret_daily, Length: 2304, dtype: float64
1d forecast: 0.34462397008645324
5d forecast: 0.37337926064681654
21d forecast: 0.4533658621316262


In [73]:
# 1. Select returns up to the forecast date
forecast_date = "2020-12-31"
subset = returns_daily.loc[:forecast_date]

# 2. Fit GARCH on data up to forecast date
garch = GARCHVolatilityForecaster(subset)
garch.fit()

# 3. Forecast next 7-day volatility (annualized)
horizon = 7
forecast_vol = garch.forecast(horizon=horizon)

# 4. Compute realized volatility over the next 7 days
realized_vol_series = realized_future_vol(df, h=horizon, freq="daily")

# Get the realized vol for the period AFTER forecast_date

# realized vol ending at forecast_date + horizon
realized_date = pd.Timestamp(forecast_date) + pd.Timedelta(days=horizon)

realized_vol = realized_vol_series.loc[realized_date]

# 5. Print results
print(f"Forecast date: {forecast_date}")
print(f"Forecasted {horizon}-day vol (annualized): {forecast_vol:.2%}")
if realized_vol is not None:
    print(f"Realized {horizon}-day vol (annualized): {realized_vol:.2%}")
else:
    print("No realized volatility available for this forecast horizon.")

# (Optional) show last few returns used for fitting
print("\nLast few returns in fitting subset:")
print(subset.tail())


KeyError: Timestamp('2021-01-07 00:00:00')

In [ ]:
# Parameters
forecast_date = pd.Timestamp("2020-12-31", tz="UTC")
horizon = 7

# 1. Select returns up to the forecast date
subset = returns_daily.loc[:forecast_date]

# 2. Fit GARCH on data up to forecast date
garch = GARCHVolatilityForecaster(subset)
garch.fit()

# 3. Forecast next h-day volatility (annualized)
forecast_vol = garch.forecast(horizon=horizon)

# 4. Compute realized volatility over the next h days
realized_vol_series = realized_future_vol(df, h=horizon, freq="daily")

# Align realized vol: ending at forecast_date + horizon
realized_date = forecast_date + pd.Timedelta(days=horizon)

# Safer lookup with .get()
realized_vol = realized_vol_series.get(realized_date, None)

# 5. Print results
print("=" * 60)
print(f" Forecast Evaluation (horizon = {horizon} days)")
print("-" * 60)
print(f" Forecast date: {forecast_date.date()}")
print(f" Forecasted vol (annualized): {forecast_vol:.2%}")
if realized_vol is not None:
    print(f" Realized vol  (annualized): {realized_vol:.2%}")
else:
    print(f" ⚠️ No realized volatility available for {realized_date.date()}")
print("=" * 60)

# # (Optional) show last few returns used for fitting
# print("\nLast few returns in fitting subset:")
# print(subset.tail())


 Forecast Evaluation (horizon = 7 days)
------------------------------------------------------------
 Forecast date: 2020-12-31
 Forecasted vol (annualized): 68.93%
 Realized vol  (annualized): 10547.46%


Putting It All Together

At each date in your backtest:

Ex-ante decision

Compare FV vs. IV

Generate trading signal (long or short straddle).

Ex-post evaluation

Compare RV vs. FV → did your model forecast well?

Compare RV vs. IV → did your trade (based on IV vs. FV) pay off?